In [1]:
import matplotlib
# matplotlib.use('Agg')
import matplotlib.pyplot as plt
import copy
import numpy as np
from torchvision import datasets, transforms
import torch

from utils.sampling import mnist_iid, mnist_noniid, cifar_iid, cifar_noniid, cifar_noniid_shared
from utils.options import args_parser
from models.Update import LocalUpdate
from models.Nets import MLP, CNNMnist, CNNCifar, LeNet, CNNMnist2
from models.Fed import FedAvg
from models.Fed import FedQAvg, Quantization, Quantization_Finite, my_score, my_score_Finite
from models.test import test_img


import math


# from sympy import * 
from utils.functions import *

%load_ext autoreload
%autoreload 2

In [2]:
class my_argument:    
    epochs = 200    #"rounds of training"
    num_users = 120  # "number of users: K"
    frac = 0.5 #"the fraction of clients: C"
    local_ep=1 #"the number of local epochs: E"
    local_bs=50 #"local batch size: B"
    bs=50 #"test batch size"
    lr=0.01 #"learning rate"
    momentum=0.9 # "SGD momentum (default: 0.5)"
    split='user' # "train-test split type, user or sample"
    weight_decay = 5e-4
    opt = 'SGD' #'ADAM'
    loss = 'Cross'

    # model arguments
    model = 'cnn'
    kernel_num=9 #, help='number of each kind of kernel')
    kernel_sizes='3,4,5' #  help='comma-separated kernel size to use for convolution')
    norm='batch_norm' #, help="batch_norm, layer_norm, or None")
    num_filters=32 #, help="number of filters for conv nets")
    max_pool='True' #help="Whether use max pooling rather than strided convolutions")

    # other arguments
    dataset='cifar' #, help="name of dataset")
    iid=0
    num_classes=10#, help="number of classes")
    num_channels=1#, help="number of channels of imges")
    gpu=1#, help="GPU ID, -1 for CPU")
    stopping_rounds=10#, help='rounds of early stopping')
    verbose='False'#, help='verbose print')
    seed=1#, help='random seed (default: 1)')
    
args = my_argument()

args.device = torch.device('cuda:{}'.format(args.gpu) if torch.cuda.is_available() and args.gpu != -1 else 'cpu')

use_cuda = torch.cuda.is_available()
print(use_cuda)
args.device = torch.device("cuda" if use_cuda else "cpu")
print(args.device)

True
cuda


In [3]:
from torchvision import datasets, transforms


trans_cifar = transforms.Compose([transforms.ToTensor(), transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))])
dataset_train = datasets.CIFAR10('./data/cifar', train=True, download=True, transform=trans_cifar)
dataset_test = datasets.CIFAR10('./data/cifar', train=False, download=True, transform=trans_cifar)


Files already downloaded and verified
Files already downloaded and verified


In [4]:
dict_users = cifar_noniid_shared(dataset_train, args.num_users)

number of non-shared images= 415
number of shared images= 200
number of images per user= 615


## Assign Dropout Probability

In [5]:
N = 120
K = 12

# p_per_class = np.array([-0.1, -0.05, 0 , 0.05, 0.1, 0.15, 0.2, 0.25, 0.3, 0.35])+0.025

p_per_class = np.array([0.1, 0.15, 0.2, 0.25, 0.3, 0.3, 0.35, 0.4, 0.45, 0.5])
print(p_per_class)

p_per_user = np.zeros((N,))

hist_ = np.zeros((10,))

for i in range(N):
    idxs=dict_users[i].astype(int)
    target = np.array(dataset_train.targets)
    cur_labels = target[idxs]
#     print(np.shape(target))
#     print(target[idxs])
    
    label_first = int(cur_labels[0])
    label_second = int(cur_labels[-1])
    
#     print(i,cur_labels)
    print(i,label_first,label_second)
    
    hist_[label_first] += 1
    
    p_per_user[i] = p_per_class[label_first]
#     print(p_per_class[label_first] + p_per_class[label_second], p_per_user[i])
print(p_per_user)

print("hist",hist_)

print(np.sum(p_per_user)/120)

[0.1  0.15 0.2  0.25 0.3  0.3  0.35 0.4  0.45 0.5 ]
0 2 9
1 7 9
2 3 9
3 7 9
4 8 9
5 6 9
6 5 9
7 1 9
8 8 9
9 7 9
10 9 9
11 1 9
12 5 9
13 6 9
14 2 9
15 0 9
16 8 9
17 9 9
18 3 9
19 2 9
20 1 9
21 3 9
22 6 9
23 4 9
24 5 9
25 2 9
26 5 9
27 6 9
28 9 9
29 5 9
30 5 9
31 1 9
32 7 9
33 2 9
34 2 9
35 1 9
36 9 9
37 5 9
38 3 9
39 7 9
40 7 9
41 0 9
42 7 9
43 8 9
44 0 9
45 6 9
46 0 9
47 9 9
48 7 9
49 8 9
50 1 9
51 1 9
52 4 9
53 3 9
54 8 9
55 5 9
56 9 9
57 1 9
58 8 9
59 0 9
60 5 9
61 9 9
62 0 9
63 4 9
64 0 9
65 4 9
66 3 9
67 2 9
68 9 9
69 0 9
70 9 9
71 4 9
72 9 9
73 5 9
74 2 9
75 6 9
76 0 9
77 4 9
78 6 9
79 6 9
80 6 9
81 2 9
82 4 9
83 6 9
84 4 9
85 4 9
86 0 9
87 7 9
88 1 9
89 8 9
90 3 9
91 3 9
92 2 9
93 1 9
94 1 9
95 4 9
96 7 9
97 3 9
98 8 9
99 4 9
100 4 9
101 9 9
102 5 9
103 7 9
104 3 9
105 3 9
106 5 9
107 9 9
108 6 9
109 8 9
110 3 9
111 7 9
112 6 9
113 1 9
114 2 9
115 8 9
116 0 9
117 2 9
118 8 9
119 0 9
[0.2  0.4  0.25 0.4  0.45 0.35 0.3  0.15 0.45 0.4  0.5  0.15 0.3  0.35
 0.2  0.1  0.45 0.5  0.25 0

# 1. Random Selection (FedAvg)

In [52]:
from models.Nets import NIN,CNN_moderate, CNNCifar3

p = 0.3
N = 120
K = 12

N_trials = 5
Max_iter = 1000

args.opt = 'SGD'

lr_array = [0.01]

args.local_ep = 1
args.local_bs = 50
args.weight_decay = 5e-4

acc_test_arr_random  = np.zeros((len(lr_array),N_trials,Max_iter))
loss_test_arr_random = np.zeros((len(lr_array),N_trials,Max_iter))

P_random = []

for lr_idx in range(len(lr_array)):
    
    for trial_idx in range(N_trials):
        
        args.lr       = lr_array[lr_idx]
        
        net_glob = CNNCifar3(args)
        
        net_glob = net_glob.cuda()
        
        print(net_glob)

        net_glob.train()
        
        P_random = []

        # copy weights
        w_glob = net_glob.state_dict()
        for iter in range(Max_iter): #args.epochs
            
            
            if iter == 400 or iter == 800:
                args.lr = args.lr * 0.4
            
            print('lr=',args.lr)
            
            w_locals, loss_locals = [], []

            ###############################
            # 0. Dropout Realization
            ###############################    
            
            u = np.ones((N,))
            for u_idx in range(N):
                p_sel = p_per_user[u_idx]
                u[u_idx] = np.random.binomial(1, 1-p_sel, size=1)[0]
            
            result = np.where(u == 1)
            drop_result = np.where(u == 0)

            ###############################
            # 1. Weighted Random Selection
            ###############################

            #idxs_users = np.random.choice(range(N), K, replace=False)
            
            idxs_users = np.random.choice(result[0], K, replace=False)


            p_tmp = np.zeros(N)
            p_tmp[idxs_users] = 1

            P_random.append(p_tmp)

        #     idxs_users = np.random.choice(range(N), K, replace=False)
            for idx in idxs_users:
        #         print(idx)
                local = LocalUpdate(args=args, dataset=dataset_train, idxs=dict_users[idx])
                w, loss = local.train(net=copy.deepcopy(net_glob).to(args.device))
                w_locals.append(copy.deepcopy(w))
                loss_locals.append(copy.deepcopy(loss))
            # update global weights
            w_glob = FedAvg(w_locals)

            # copy weight to net_glob
            net_glob.load_state_dict(w_glob)

            # print loss
            loss_avg = sum(loss_locals) / len(loss_locals)

            #loss_train.append(loss_avg)

            acc_test, loss_test = test_img(net_glob, dataset_test, args)
            acc_test_arr_random[lr_idx][trial_idx][iter]  = acc_test
            loss_test_arr_random[lr_idx][trial_idx][iter] = loss_test
            if iter % 1 ==0:
                print('Round {:3d}, Train average loss {:.3f} Test accuracy {:.3f}'.format(iter, loss_avg,acc_test))
            #print(loss_train)

CNNCifar3(
  (conv1): Conv2d(3, 6, kernel_size=(5, 5), stride=(1, 1))
  (pool): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv2): Conv2d(6, 16, kernel_size=(5, 5), stride=(1, 1))
  (fc1): Linear(in_features=400, out_features=120, bias=True)
  (fc2): Linear(in_features=120, out_features=84, bias=True)
  (fc3): Linear(in_features=84, out_features=10, bias=True)
  (dropout): Dropout(p=0.2, inplace=False)
)
lr= 0.01

Test set: Average loss: 2.3271 
Accuracy: 1000/10000 (10.00%)

Round   0, Train average loss 1.956 Test accuracy 10.000
lr= 0.01

Test set: Average loss: 2.3031 
Accuracy: 1164/10000 (11.64%)

Round   1, Train average loss 1.607 Test accuracy 11.640
lr= 0.01

Test set: Average loss: 2.3025 
Accuracy: 1391/10000 (13.91%)

Round   2, Train average loss 1.807 Test accuracy 13.910
lr= 0.01

Test set: Average loss: 2.2800 
Accuracy: 1530/10000 (15.30%)

Round   3, Train average loss 1.697 Test accuracy 15.300
lr= 0.01

Test set: Average loss: 2.2


Test set: Average loss: 1.8877 
Accuracy: 3004/10000 (30.04%)

Round  60, Train average loss 1.165 Test accuracy 30.040
lr= 0.01

Test set: Average loss: 1.9162 
Accuracy: 3031/10000 (30.31%)

Round  61, Train average loss 1.246 Test accuracy 30.310
lr= 0.01

Test set: Average loss: 1.8822 
Accuracy: 3120/10000 (31.20%)

Round  62, Train average loss 1.216 Test accuracy 31.200
lr= 0.01

Test set: Average loss: 1.8833 
Accuracy: 3130/10000 (31.30%)

Round  63, Train average loss 1.221 Test accuracy 31.300
lr= 0.01

Test set: Average loss: 1.8497 
Accuracy: 3235/10000 (32.35%)

Round  64, Train average loss 1.152 Test accuracy 32.350
lr= 0.01

Test set: Average loss: 1.8716 
Accuracy: 3094/10000 (30.94%)

Round  65, Train average loss 1.161 Test accuracy 30.940
lr= 0.01

Test set: Average loss: 1.8564 
Accuracy: 3207/10000 (32.07%)

Round  66, Train average loss 1.124 Test accuracy 32.070
lr= 0.01

Test set: Average loss: 1.8635 
Accuracy: 3188/10000 (31.88%)

Round  67, Train average l


Test set: Average loss: 1.7310 
Accuracy: 3736/10000 (37.36%)

Round 124, Train average loss 0.781 Test accuracy 37.360
lr= 0.01

Test set: Average loss: 1.7371 
Accuracy: 3639/10000 (36.39%)

Round 125, Train average loss 0.797 Test accuracy 36.390
lr= 0.01

Test set: Average loss: 1.7504 
Accuracy: 3546/10000 (35.46%)

Round 126, Train average loss 0.729 Test accuracy 35.460
lr= 0.01

Test set: Average loss: 1.7421 
Accuracy: 3636/10000 (36.36%)

Round 127, Train average loss 0.795 Test accuracy 36.360
lr= 0.01

Test set: Average loss: 1.8576 
Accuracy: 3178/10000 (31.78%)

Round 128, Train average loss 0.833 Test accuracy 31.780
lr= 0.01

Test set: Average loss: 1.7303 
Accuracy: 3714/10000 (37.14%)

Round 129, Train average loss 0.747 Test accuracy 37.140
lr= 0.01

Test set: Average loss: 1.7473 
Accuracy: 3544/10000 (35.44%)

Round 130, Train average loss 0.679 Test accuracy 35.440
lr= 0.01

Test set: Average loss: 1.7198 
Accuracy: 3702/10000 (37.02%)

Round 131, Train average l


Test set: Average loss: 1.6812 
Accuracy: 3826/10000 (38.26%)

Round 188, Train average loss 0.591 Test accuracy 38.260
lr= 0.01

Test set: Average loss: 1.7370 
Accuracy: 3665/10000 (36.65%)

Round 189, Train average loss 0.608 Test accuracy 36.650
lr= 0.01

Test set: Average loss: 1.7050 
Accuracy: 3797/10000 (37.97%)

Round 190, Train average loss 0.635 Test accuracy 37.970
lr= 0.01

Test set: Average loss: 1.7480 
Accuracy: 3537/10000 (35.37%)

Round 191, Train average loss 0.602 Test accuracy 35.370
lr= 0.01

Test set: Average loss: 1.7273 
Accuracy: 3744/10000 (37.44%)

Round 192, Train average loss 0.661 Test accuracy 37.440
lr= 0.01

Test set: Average loss: 1.7642 
Accuracy: 3284/10000 (32.84%)

Round 193, Train average loss 0.653 Test accuracy 32.840
lr= 0.01

Test set: Average loss: 1.7255 
Accuracy: 3771/10000 (37.71%)

Round 194, Train average loss 0.569 Test accuracy 37.710
lr= 0.01

Test set: Average loss: 1.7103 
Accuracy: 3781/10000 (37.81%)

Round 195, Train average l


Test set: Average loss: 1.6668 
Accuracy: 3848/10000 (38.48%)

Round 252, Train average loss 0.527 Test accuracy 38.480
lr= 0.01

Test set: Average loss: 1.6842 
Accuracy: 3900/10000 (39.00%)

Round 253, Train average loss 0.491 Test accuracy 39.000
lr= 0.01

Test set: Average loss: 1.6614 
Accuracy: 3892/10000 (38.92%)

Round 254, Train average loss 0.490 Test accuracy 38.920
lr= 0.01

Test set: Average loss: 1.7006 
Accuracy: 3829/10000 (38.29%)

Round 255, Train average loss 0.560 Test accuracy 38.290
lr= 0.01

Test set: Average loss: 1.6314 
Accuracy: 4009/10000 (40.09%)

Round 256, Train average loss 0.524 Test accuracy 40.090
lr= 0.01

Test set: Average loss: 1.7371 
Accuracy: 3816/10000 (38.16%)

Round 257, Train average loss 0.557 Test accuracy 38.160
lr= 0.01

Test set: Average loss: 1.6178 
Accuracy: 4104/10000 (41.04%)

Round 258, Train average loss 0.532 Test accuracy 41.040
lr= 0.01

Test set: Average loss: 1.7505 
Accuracy: 3614/10000 (36.14%)

Round 259, Train average l

...


Test set: Average loss: 1.4589 
Accuracy: 4644/10000 (46.44%)

Round 735, Train average loss 0.309 Test accuracy 46.440
lr= 0.004

Test set: Average loss: 1.4731 
Accuracy: 4638/10000 (46.38%)

Round 736, Train average loss 0.275 Test accuracy 46.380
lr= 0.004

Test set: Average loss: 1.5092 
Accuracy: 4570/10000 (45.70%)

Round 737, Train average loss 0.274 Test accuracy 45.700
lr= 0.004

Test set: Average loss: 1.4825 
Accuracy: 4704/10000 (47.04%)

Round 738, Train average loss 0.291 Test accuracy 47.040
lr= 0.004

Test set: Average loss: 1.5526 
Accuracy: 4316/10000 (43.16%)

Round 739, Train average loss 0.290 Test accuracy 43.160
lr= 0.004

Test set: Average loss: 1.5073 
Accuracy: 4611/10000 (46.11%)

Round 740, Train average loss 0.331 Test accuracy 46.110
lr= 0.004

Test set: Average loss: 1.4821 
Accuracy: 4709/10000 (47.09%)

Round 741, Train average loss 0.320 Test accuracy 47.090
lr= 0.004

Test set: Average loss: 1.7234 
Accuracy: 3891/10000 (38.91%)

Round 742, Train av


Test set: Average loss: 1.5210 
Accuracy: 4436/10000 (44.36%)

Round 798, Train average loss 0.267 Test accuracy 44.360
lr= 0.004

Test set: Average loss: 1.5452 
Accuracy: 4515/10000 (45.15%)

Round 799, Train average loss 0.331 Test accuracy 45.150
lr= 0.0016

Test set: Average loss: 1.4613 
Accuracy: 4701/10000 (47.01%)

Round 800, Train average loss 0.430 Test accuracy 47.010
lr= 0.0016

Test set: Average loss: 1.4271 
Accuracy: 4758/10000 (47.58%)

Round 801, Train average loss 0.373 Test accuracy 47.580
lr= 0.0016

Test set: Average loss: 1.4594 
Accuracy: 4713/10000 (47.13%)

Round 802, Train average loss 0.378 Test accuracy 47.130
lr= 0.0016

Test set: Average loss: 1.3617 
Accuracy: 5102/10000 (51.02%)

Round 803, Train average loss 0.440 Test accuracy 51.020
lr= 0.0016

Test set: Average loss: 1.3876 
Accuracy: 5027/10000 (50.27%)

Round 804, Train average loss 0.368 Test accuracy 50.270
lr= 0.0016

Test set: Average loss: 1.4447 
Accuracy: 4811/10000 (48.11%)

Round 805, Tr


Test set: Average loss: 1.5791 
Accuracy: 4424/10000 (44.24%)

Round 861, Train average loss 0.317 Test accuracy 44.240
lr= 0.0016

Test set: Average loss: 1.3819 
Accuracy: 4995/10000 (49.95%)

Round 862, Train average loss 0.310 Test accuracy 49.950
lr= 0.0016

Test set: Average loss: 1.3649 
Accuracy: 5102/10000 (51.02%)

Round 863, Train average loss 0.355 Test accuracy 51.020
lr= 0.0016

Test set: Average loss: 1.3844 
Accuracy: 5000/10000 (50.00%)

Round 864, Train average loss 0.282 Test accuracy 50.000
lr= 0.0016

Test set: Average loss: 1.6871 
Accuracy: 4119/10000 (41.19%)

Round 865, Train average loss 0.311 Test accuracy 41.190
lr= 0.0016

Test set: Average loss: 1.3702 
Accuracy: 5044/10000 (50.44%)

Round 866, Train average loss 0.277 Test accuracy 50.440
lr= 0.0016

Test set: Average loss: 1.6801 
Accuracy: 4120/10000 (41.20%)

Round 867, Train average loss 0.289 Test accuracy 41.200
lr= 0.0016

Test set: Average loss: 1.4336 
Accuracy: 4721/10000 (47.21%)

Round 868, T


Test set: Average loss: 1.3987 
Accuracy: 4897/10000 (48.97%)

Round 924, Train average loss 0.321 Test accuracy 48.970
lr= 0.0016

Test set: Average loss: 1.7445 
Accuracy: 3950/10000 (39.50%)

Round 925, Train average loss 0.322 Test accuracy 39.500
lr= 0.0016

Test set: Average loss: 1.5742 
Accuracy: 4387/10000 (43.87%)

Round 926, Train average loss 0.317 Test accuracy 43.870
lr= 0.0016

Test set: Average loss: 1.4715 
Accuracy: 4739/10000 (47.39%)

Round 927, Train average loss 0.374 Test accuracy 47.390
lr= 0.0016

Test set: Average loss: 1.4705 
Accuracy: 4645/10000 (46.45%)

Round 928, Train average loss 0.314 Test accuracy 46.450
lr= 0.0016

Test set: Average loss: 1.4290 
Accuracy: 4903/10000 (49.03%)

Round 929, Train average loss 0.282 Test accuracy 49.030
lr= 0.0016

Test set: Average loss: 1.5846 
Accuracy: 4391/10000 (43.91%)

Round 930, Train average loss 0.305 Test accuracy 43.910
lr= 0.0016

Test set: Average loss: 1.5853 
Accuracy: 4166/10000 (41.66%)

Round 931, T


Test set: Average loss: 1.6502 
Accuracy: 4062/10000 (40.62%)

Round 987, Train average loss 0.321 Test accuracy 40.620
lr= 0.0016

Test set: Average loss: 1.7120 
Accuracy: 3920/10000 (39.20%)

Round 988, Train average loss 0.312 Test accuracy 39.200
lr= 0.0016

Test set: Average loss: 1.3953 
Accuracy: 4900/10000 (49.00%)

Round 989, Train average loss 0.299 Test accuracy 49.000
lr= 0.0016

Test set: Average loss: 1.5195 
Accuracy: 4595/10000 (45.95%)

Round 990, Train average loss 0.338 Test accuracy 45.950
lr= 0.0016

Test set: Average loss: 1.3728 
Accuracy: 5039/10000 (50.39%)

Round 991, Train average loss 0.293 Test accuracy 50.390
lr= 0.0016

Test set: Average loss: 1.7873 
Accuracy: 3650/10000 (36.50%)

Round 992, Train average loss 0.290 Test accuracy 36.500
lr= 0.0016

Test set: Average loss: 1.5519 
Accuracy: 4323/10000 (43.23%)

Round 993, Train average loss 0.324 Test accuracy 43.230
lr= 0.0016

Test set: Average loss: 1.4027 
Accuracy: 4896/10000 (48.96%)

Round 994, T

# 2. Weighted Random Selection

In [53]:
from models.Nets import NIN,CNN_moderate, CNNCifar3

lr_array = [0.01]


args.local_ep = 1
args.local_bs = 50
args.weight_decay = 5e-4

N = 120
K = 12

N_trials = 5
Max_iter = 1000

args.opt = 'SGD'

args.local_ep = 1
args.local_bs = 50


acc_test_arr_w_random_asymDrop  = np.zeros((len(lr_array), N_trials, Max_iter))
loss_test_arr_w_random_asymDrop = np.zeros((len(lr_array), N_trials, Max_iter))


for trial_idx in range(N_trials):
    
    for lr_idx in range(len(lr_array)):
        
        args.lr = lr_array[lr_idx]
        
        P_w_random_asymDrop = []
        
        print()
        print('Learning Rate =',args.lr)
        print()
        net_glob = CNNCifar3(args)
        net_glob = net_glob.cuda()
        print(net_glob)

        net_glob.train()

        # copy weights
        w_glob = net_glob.state_dict()
        for iter in range(Max_iter): #args.epochs
            w_locals, loss_locals = [], []
            
            if iter == 400 or iter == 800:
                args.lr = args.lr * 0.4
                
                
            ###############################
            # 0. Dropout Realization
            ###############################    
            
            u = np.ones((N,))
            for u_idx in range(N):
                p_sel = p_per_user[u_idx]
                u[u_idx] = np.random.binomial(1, 1-p_sel, size=1)[0]
            
            result = np.where(u == 1)
            drop_result = np.where(u == 0)

            ###############################
            # 1. Weighted Random Selection
            ###############################

            if iter == 0:
                idxs_users = np.random.choice(result[0], K, replace=False)
#                 print('select=',select)
            else:
                P = np.array(P_w_random_asymDrop)
                P_sum = np.sum(P, axis=0).astype(int)
        
                for i in drop_result[0]:
                    P_sum[i] = Max_iter + 1   

                P_sum_sort = P_sum.argsort()

                idxs_users = P_sum_sort[:K]
            

            p_tmp = np.zeros(N)
            p_tmp[idxs_users] = 1

            P_w_random_asymDrop.append(p_tmp)


        #     idxs_users = np.random.choice(range(N), K, replace=False)
            for idx in idxs_users:
        #         print(idx)
                local = LocalUpdate(args=args, dataset=dataset_train, idxs=dict_users[idx])
                w, loss = local.train(net=copy.deepcopy(net_glob).to(args.device))
                w_locals.append(copy.deepcopy(w))
                loss_locals.append(copy.deepcopy(loss))
            # update global weights
            w_glob = FedAvg(w_locals)

            # copy weight to net_glob
            net_glob.load_state_dict(w_glob)

            # print loss
            loss_avg = sum(loss_locals) / len(loss_locals)

    #         loss_train.append(loss_avg)

            acc_test, loss_test = test_img(net_glob, dataset_test, args)
            acc_test_arr_w_random_asymDrop[lr_idx][trial_idx][iter]  = acc_test
            loss_test_arr_w_random_asymDrop[lr_idx][trial_idx][iter] = loss_test
            if iter % 1 ==0:
                print('Round {:3d}, Train average loss {:.3f} Test accuracy {:.3f}'.format(iter, loss_avg,acc_test))
            #print(loss_train)


Learning Rate = 0.01

CNNCifar3(
  (conv1): Conv2d(3, 6, kernel_size=(5, 5), stride=(1, 1))
  (pool): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv2): Conv2d(6, 16, kernel_size=(5, 5), stride=(1, 1))
  (fc1): Linear(in_features=400, out_features=120, bias=True)
  (fc2): Linear(in_features=120, out_features=84, bias=True)
  (fc3): Linear(in_features=84, out_features=10, bias=True)
  (dropout): Dropout(p=0.2, inplace=False)
)

Test set: Average loss: 2.3153 
Accuracy: 1117/10000 (11.17%)

Round   0, Train average loss 1.928 Test accuracy 11.170

Test set: Average loss: 2.3047 
Accuracy: 1089/10000 (10.89%)

Round   1, Train average loss 1.702 Test accuracy 10.890

Test set: Average loss: 2.2989 
Accuracy: 1186/10000 (11.86%)

Round   2, Train average loss 1.786 Test accuracy 11.860

Test set: Average loss: 2.2989 
Accuracy: 1331/10000 (13.31%)

Round   3, Train average loss 1.685 Test accuracy 13.310

Test set: Average loss: 2.3190 
Accuracy: 1000/10


Test set: Average loss: 1.7800 
Accuracy: 3500/10000 (35.00%)

Round  64, Train average loss 1.033 Test accuracy 35.000

Test set: Average loss: 1.8110 
Accuracy: 3488/10000 (34.88%)

Round  65, Train average loss 1.020 Test accuracy 34.880

Test set: Average loss: 1.8017 
Accuracy: 3483/10000 (34.83%)

Round  66, Train average loss 1.024 Test accuracy 34.830

Test set: Average loss: 1.7809 
Accuracy: 3734/10000 (37.34%)

Round  67, Train average loss 1.060 Test accuracy 37.340

Test set: Average loss: 1.7492 
Accuracy: 3795/10000 (37.95%)

Round  68, Train average loss 0.988 Test accuracy 37.950

Test set: Average loss: 1.7911 
Accuracy: 3638/10000 (36.38%)

Round  69, Train average loss 1.058 Test accuracy 36.380

Test set: Average loss: 1.7530 
Accuracy: 3609/10000 (36.09%)

Round  70, Train average loss 1.019 Test accuracy 36.090

Test set: Average loss: 1.7555 
Accuracy: 3710/10000 (37.10%)

Round  71, Train average loss 1.020 Test accuracy 37.100

Test set: Average loss: 1.7802 


Test set: Average loss: 1.7021 
Accuracy: 3875/10000 (38.75%)

Round 132, Train average loss 0.753 Test accuracy 38.750

Test set: Average loss: 1.6970 
Accuracy: 3748/10000 (37.48%)

Round 133, Train average loss 0.750 Test accuracy 37.480

Test set: Average loss: 1.6692 
Accuracy: 3989/10000 (39.89%)

Round 134, Train average loss 0.635 Test accuracy 39.890

Test set: Average loss: 1.6802 
Accuracy: 3859/10000 (38.59%)

Round 135, Train average loss 0.654 Test accuracy 38.590

Test set: Average loss: 1.6626 
Accuracy: 3967/10000 (39.67%)

Round 136, Train average loss 0.689 Test accuracy 39.670

Test set: Average loss: 1.6760 
Accuracy: 3899/10000 (38.99%)

Round 137, Train average loss 0.655 Test accuracy 38.990

Test set: Average loss: 1.6733 
Accuracy: 4008/10000 (40.08%)

Round 138, Train average loss 0.716 Test accuracy 40.080

Test set: Average loss: 1.6596 
Accuracy: 3940/10000 (39.40%)

Round 139, Train average loss 0.638 Test accuracy 39.400

Test set: Average loss: 1.7068 


Test set: Average loss: 1.6328 
Accuracy: 4013/10000 (40.13%)

Round 200, Train average loss 0.568 Test accuracy 40.130

Test set: Average loss: 1.6627 
Accuracy: 4030/10000 (40.30%)

Round 201, Train average loss 0.565 Test accuracy 40.300

Test set: Average loss: 1.6151 
Accuracy: 4165/10000 (41.65%)

Round 202, Train average loss 0.545 Test accuracy 41.650

Test set: Average loss: 1.6266 
Accuracy: 4054/10000 (40.54%)

Round 203, Train average loss 0.574 Test accuracy 40.540

Test set: Average loss: 1.7870 
Accuracy: 3492/10000 (34.92%)

Round 204, Train average loss 0.586 Test accuracy 34.920

Test set: Average loss: 1.6295 
Accuracy: 4025/10000 (40.25%)

Round 205, Train average loss 0.624 Test accuracy 40.250

Test set: Average loss: 1.6674 
Accuracy: 3955/10000 (39.55%)

Round 206, Train average loss 0.593 Test accuracy 39.550

Test set: Average loss: 1.6693 
Accuracy: 3953/10000 (39.53%)

Round 207, Train average loss 0.598 Test accuracy 39.530

Test set: Average loss: 1.6576 


Test set: Average loss: 1.5529 
Accuracy: 4443/10000 (44.43%)

Round 268, Train average loss 0.495 Test accuracy 44.430

Test set: Average loss: 1.6433 
Accuracy: 4145/10000 (41.45%)

Round 269, Train average loss 0.494 Test accuracy 41.450

Test set: Average loss: 1.6295 
Accuracy: 4082/10000 (40.82%)

Round 270, Train average loss 0.506 Test accuracy 40.820

Test set: Average loss: 1.6381 
Accuracy: 4208/10000 (42.08%)

Round 271, Train average loss 0.548 Test accuracy 42.080

Test set: Average loss: 1.6259 
Accuracy: 4155/10000 (41.55%)

Round 272, Train average loss 0.456 Test accuracy 41.550

Test set: Average loss: 1.5636 
Accuracy: 4372/10000 (43.72%)

Round 273, Train average loss 0.541 Test accuracy 43.720

Test set: Average loss: 1.5632 
Accuracy: 4340/10000 (43.40%)

Round 274, Train average loss 0.503 Test accuracy 43.400

Test set: Average loss: 1.5511 
Accuracy: 4408/10000 (44.08%)

Round 275, Train average loss 0.477 Test accuracy 44.080

Test set: Average loss: 1.5429 

...


Test set: Average loss: 1.5684 
Accuracy: 4350/10000 (43.50%)

Round 672, Train average loss 0.383 Test accuracy 43.500

Test set: Average loss: 1.5394 
Accuracy: 4466/10000 (44.66%)

Round 673, Train average loss 0.366 Test accuracy 44.660

Test set: Average loss: 1.5442 
Accuracy: 4295/10000 (42.95%)

Round 674, Train average loss 0.304 Test accuracy 42.950

Test set: Average loss: 1.5344 
Accuracy: 4394/10000 (43.94%)

Round 675, Train average loss 0.331 Test accuracy 43.940

Test set: Average loss: 1.4497 
Accuracy: 4742/10000 (47.42%)

Round 676, Train average loss 0.427 Test accuracy 47.420

Test set: Average loss: 1.5801 
Accuracy: 4377/10000 (43.77%)

Round 677, Train average loss 0.370 Test accuracy 43.770

Test set: Average loss: 1.6002 
Accuracy: 4312/10000 (43.12%)

Round 678, Train average loss 0.374 Test accuracy 43.120

Test set: Average loss: 1.4964 
Accuracy: 4472/10000 (44.72%)

Round 679, Train average loss 0.388 Test accuracy 44.720

Test set: Average loss: 1.4077 


Test set: Average loss: 1.6853 
Accuracy: 4152/10000 (41.52%)

Round 740, Train average loss 0.342 Test accuracy 41.520

Test set: Average loss: 1.4674 
Accuracy: 4749/10000 (47.49%)

Round 741, Train average loss 0.279 Test accuracy 47.490

Test set: Average loss: 1.5252 
Accuracy: 4323/10000 (43.23%)

Round 742, Train average loss 0.335 Test accuracy 43.230

Test set: Average loss: 1.4578 
Accuracy: 4736/10000 (47.36%)

Round 743, Train average loss 0.331 Test accuracy 47.360

Test set: Average loss: 1.4154 
Accuracy: 4821/10000 (48.21%)

Round 744, Train average loss 0.326 Test accuracy 48.210

Test set: Average loss: 1.4107 
Accuracy: 4896/10000 (48.96%)

Round 745, Train average loss 0.281 Test accuracy 48.960

Test set: Average loss: 1.6279 
Accuracy: 4109/10000 (41.09%)

Round 746, Train average loss 0.319 Test accuracy 41.090

Test set: Average loss: 1.4720 
Accuracy: 4761/10000 (47.61%)

Round 747, Train average loss 0.357 Test accuracy 47.610

Test set: Average loss: 1.4193 


Test set: Average loss: 1.4178 
Accuracy: 4890/10000 (48.90%)

Round 808, Train average loss 0.378 Test accuracy 48.900

Test set: Average loss: 1.4122 
Accuracy: 4986/10000 (49.86%)

Round 809, Train average loss 0.356 Test accuracy 49.860

Test set: Average loss: 1.4039 
Accuracy: 4935/10000 (49.35%)

Round 810, Train average loss 0.339 Test accuracy 49.350

Test set: Average loss: 1.4924 
Accuracy: 4678/10000 (46.78%)

Round 811, Train average loss 0.338 Test accuracy 46.780

Test set: Average loss: 1.4169 
Accuracy: 4875/10000 (48.75%)

Round 812, Train average loss 0.318 Test accuracy 48.750

Test set: Average loss: 1.5357 
Accuracy: 4471/10000 (44.71%)

Round 813, Train average loss 0.339 Test accuracy 44.710

Test set: Average loss: 1.4787 
Accuracy: 4626/10000 (46.26%)

Round 814, Train average loss 0.372 Test accuracy 46.260

Test set: Average loss: 1.4022 
Accuracy: 4962/10000 (49.62%)

Round 815, Train average loss 0.299 Test accuracy 49.620

Test set: Average loss: 1.3902 


Test set: Average loss: 1.5603 
Accuracy: 4341/10000 (43.41%)

Round 876, Train average loss 0.363 Test accuracy 43.410

Test set: Average loss: 1.3722 
Accuracy: 5100/10000 (51.00%)

Round 877, Train average loss 0.422 Test accuracy 51.000

Test set: Average loss: 1.7476 
Accuracy: 3957/10000 (39.57%)

Round 878, Train average loss 0.317 Test accuracy 39.570

Test set: Average loss: 1.4334 
Accuracy: 5019/10000 (50.19%)

Round 879, Train average loss 0.363 Test accuracy 50.190

Test set: Average loss: 1.4654 
Accuracy: 4551/10000 (45.51%)

Round 880, Train average loss 0.344 Test accuracy 45.510

Test set: Average loss: 1.4012 
Accuracy: 4951/10000 (49.51%)

Round 881, Train average loss 0.328 Test accuracy 49.510

Test set: Average loss: 1.3956 
Accuracy: 4940/10000 (49.40%)

Round 882, Train average loss 0.286 Test accuracy 49.400

Test set: Average loss: 1.6493 
Accuracy: 4243/10000 (42.43%)

Round 883, Train average loss 0.308 Test accuracy 42.430

Test set: Average loss: 1.5406 


Test set: Average loss: 1.4029 
Accuracy: 4950/10000 (49.50%)

Round 944, Train average loss 0.287 Test accuracy 49.500

Test set: Average loss: 1.5470 
Accuracy: 4513/10000 (45.13%)

Round 945, Train average loss 0.241 Test accuracy 45.130

Test set: Average loss: 1.4311 
Accuracy: 4758/10000 (47.58%)

Round 946, Train average loss 0.368 Test accuracy 47.580

Test set: Average loss: 1.4563 
Accuracy: 4735/10000 (47.35%)

Round 947, Train average loss 0.294 Test accuracy 47.350

Test set: Average loss: 1.5383 
Accuracy: 4524/10000 (45.24%)

Round 948, Train average loss 0.299 Test accuracy 45.240

Test set: Average loss: 1.4876 
Accuracy: 4599/10000 (45.99%)

Round 949, Train average loss 0.335 Test accuracy 45.990

Test set: Average loss: 1.5829 
Accuracy: 4220/10000 (42.20%)

Round 950, Train average loss 0.312 Test accuracy 42.200

Test set: Average loss: 1.5931 
Accuracy: 4418/10000 (44.18%)

Round 951, Train average loss 0.321 Test accuracy 44.180

Test set: Average loss: 1.4234 

In [54]:
import pickle

pickle.dump(acc_test_arr_random, open('./results/CIFAR_NonIID_LeNet_accuracy_Random_N120_K12_asymDrop', 'wb'), -1)
pickle.dump(acc_test_arr_w_random_asymDrop, open('./results/CIFAR_NonIID_LeNet_accuracy_w_Random_N120_K12_asymDrop', 'wb'), -1)

# 3. Partition

In [6]:
N   = 120
K   = 12

Codebook_Proposed_T6 = CodeBookDesign_Bin(N,K,4)
Codebook_Proposed_T4 = CodeBookDesign_Bin(N,K,4)
Codebook_Proposed_T3 = CodeBookDesign_Bin(N,K,3)

Codebook_Partition = CodeBookDesign_Partition(N,K)

# print(Codebook_Partition)

@CodeBookDesign_Bin, Codebook Size= 4060
@CodeBookDesign_Bin, Codebook Size= 4060
@CodeBookDesign_Bin, Codebook Size= 91389
@CodeBookDesign_Partition, Codebook Size= 10


In [59]:
from models.Nets import NIN,CNN_moderate, CNNCifar3

lr_array = [0.01]


args.local_ep = 1
args.local_bs = 50
args.weight_decay = 5e-4

N = 120
K = 12

N_trials = 3
Max_iter = 1000

args.opt = 'SGD'

args.local_ep = 1
args.local_bs = 50

acc_test_arr_Partition_N120_K12_asymDrop  = np.zeros((len(lr_array), N_trials, Max_iter))
loss_test_arr_Partition_N120_K12_asymDrop = np.zeros((len(lr_array), N_trials, Max_iter))


is_selection_applied = True
is_print = True



for trial_idx in range(N_trials):
    
    for lr_idx in range(len(lr_array)):
        
        args.lr = lr_array[lr_idx]
        
        P_partition_asymDrop = []
        
        print()
        print('Learning Rate =',args.lr)
        print()
        net_glob = CNNCifar3(args)
        net_glob = net_glob.cuda()
        print(net_glob)

        net_glob.train()

        # copy weights
        w_glob = net_glob.state_dict()
        
        for iter in range(Max_iter): #args.epochs
            w_locals, loss_locals = [], []
            
            if iter == 400 or iter == 800:
                args.lr = args.lr * 0.4

        #     u = np.random.binomial(1, 1-p, size=(N))
            u = np.ones((N,))
            for u_idx in range(N):
                p_sel = p_per_user[u_idx]
                u[u_idx] = np.random.binomial(1, 1-p_sel, size=1)[0]

            tmp = Codebook_Partition * u

            codebook_en = 1*(np.sum(tmp,axis=1) == K)

            if np.sum(codebook_en) == 0:
                if is_print:
                    print('[iter=',iter,'] @Partition, there is no available codebook')
                p_tmp = np.zeros(N)
            else:
                if is_print:
                    print('[iter=',iter,'] @Partition, Codebook selection')
                idx_en = np.where(codebook_en == 1)

                if is_selection_applied:
                    codebook_en_num = np.sum(codebook_en)
                    Codebook_En = np.reshape(Codebook_Partition[idx_en,:],(codebook_en_num,N))

                    p_tmp = UserSelection_Codebook(P_partition_asymDrop, Codebook_En)
                else:
                    idx_sel = np.random.choice(idx_en[0], 1, replace=False)
                    p_tmp = Codebook_Partition[idx_sel[0],:]

        #                 idx_sel = np.random.choice(idx_en[0], 1, replace=False)

        #                 p_tmp = Codebook_Partition[idx_sel[0],:]

            idxs_users = np.where(p_tmp == 1)

            P_partition_asymDrop.append(p_tmp)

        #     idxs_users = np.random.choice(range(args.num_users), K, replace=False)

            if np.sum(p_tmp) == K:
                for idx in idxs_users[0]:
                    print('selected idx=',idx)
                    local = LocalUpdate(args=args, dataset=dataset_train, idxs=dict_users[idx])
                    w, loss = local.train(net=copy.deepcopy(net_glob).to(args.device))
                    w_locals.append(copy.deepcopy(w))
                    loss_locals.append(copy.deepcopy(loss))
                # update global weights
                w_glob = FedAvg(w_locals)

                # copy weight to net_glob
                net_glob.load_state_dict(w_glob)

                # print loss
                loss_avg = sum(loss_locals) / len(loss_locals)

        #         loss_train.append(loss_avg)

            acc_test, loss_test = test_img(net_glob, dataset_test, args)
            acc_test_arr_Partition_N120_K12_asymDrop[lr_idx][trial_idx][iter]  = acc_test
            loss_test_arr_Partition_N120_K12_asymDrop[lr_idx][trial_idx][iter] =loss_test
            if iter % 1 ==0:
                print('Round {:3d}, Train average loss {:.3f} Test accuracy {:.3f}'.format(iter, loss_avg,acc_test))
            #print(loss_train)


Learning Rate = 0.01

CNNCifar3(
  (conv1): Conv2d(3, 6, kernel_size=(5, 5), stride=(1, 1))
  (pool): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv2): Conv2d(6, 16, kernel_size=(5, 5), stride=(1, 1))
  (fc1): Linear(in_features=400, out_features=120, bias=True)
  (fc2): Linear(in_features=120, out_features=84, bias=True)
  (fc3): Linear(in_features=84, out_features=10, bias=True)
  (dropout): Dropout(p=0.2, inplace=False)
)
[iter= 0 ] @Partition, there is no available codebook

Test set: Average loss: 2.3050 
Accuracy: 998/10000 (9.98%)

Round   0, Train average loss 0.259 Test accuracy 9.980
[iter= 1 ] @Partition, there is no available codebook

Test set: Average loss: 2.3050 
Accuracy: 998/10000 (9.98%)

Round   1, Train average loss 0.259 Test accuracy 9.980
[iter= 2 ] @Partition, there is no available codebook

Test set: Average loss: 2.3050 
Accuracy: 998/10000 (9.98%)

Round   2, Train average loss 0.259 Test accuracy 9.980
[iter= 3 ] @Partit


Test set: Average loss: 2.2972 
Accuracy: 1380/10000 (13.80%)

Round  42, Train average loss 1.675 Test accuracy 13.800
[iter= 43 ] @Partition, Codebook selection
selected idx= 60
selected idx= 61
selected idx= 62
selected idx= 63
selected idx= 64
selected idx= 65
selected idx= 66
selected idx= 67
selected idx= 68
selected idx= 69
selected idx= 70
selected idx= 71

Test set: Average loss: 2.3131 
Accuracy: 1456/10000 (14.56%)

Round  43, Train average loss 1.815 Test accuracy 14.560
[iter= 44 ] @Partition, there is no available codebook

Test set: Average loss: 2.3131 
Accuracy: 1456/10000 (14.56%)

Round  44, Train average loss 1.815 Test accuracy 14.560
[iter= 45 ] @Partition, there is no available codebook

Test set: Average loss: 2.3131 
Accuracy: 1456/10000 (14.56%)

Round  45, Train average loss 1.815 Test accuracy 14.560
[iter= 46 ] @Partition, Codebook selection
selected idx= 12
selected idx= 13
selected idx= 14
selected idx= 15
selected idx= 16
selected idx= 17
selected idx= 


Test set: Average loss: 2.2247 
Accuracy: 1560/10000 (15.60%)

Round  81, Train average loss 1.665 Test accuracy 15.600
[iter= 82 ] @Partition, there is no available codebook

Test set: Average loss: 2.2247 
Accuracy: 1560/10000 (15.60%)

Round  82, Train average loss 1.665 Test accuracy 15.600
[iter= 83 ] @Partition, there is no available codebook

Test set: Average loss: 2.2247 
Accuracy: 1560/10000 (15.60%)

Round  83, Train average loss 1.665 Test accuracy 15.600
[iter= 84 ] @Partition, there is no available codebook

Test set: Average loss: 2.2247 
Accuracy: 1560/10000 (15.60%)

Round  84, Train average loss 1.665 Test accuracy 15.600
[iter= 85 ] @Partition, there is no available codebook

Test set: Average loss: 2.2247 
Accuracy: 1560/10000 (15.60%)

Round  85, Train average loss 1.665 Test accuracy 15.600
[iter= 86 ] @Partition, Codebook selection
selected idx= 60
selected idx= 61
selected idx= 62
selected idx= 63
selected idx= 64
selected idx= 65
selected idx= 66
selected idx=


Test set: Average loss: 2.1310 
Accuracy: 2293/10000 (22.93%)

Round 122, Train average loss 1.583 Test accuracy 22.930
[iter= 123 ] @Partition, there is no available codebook

Test set: Average loss: 2.1310 
Accuracy: 2293/10000 (22.93%)

Round 123, Train average loss 1.583 Test accuracy 22.930
[iter= 124 ] @Partition, there is no available codebook

Test set: Average loss: 2.1310 
Accuracy: 2293/10000 (22.93%)

Round 124, Train average loss 1.583 Test accuracy 22.930
[iter= 125 ] @Partition, there is no available codebook

Test set: Average loss: 2.1310 
Accuracy: 2293/10000 (22.93%)

Round 125, Train average loss 1.583 Test accuracy 22.930
[iter= 126 ] @Partition, Codebook selection
selected idx= 48
selected idx= 49
selected idx= 50
selected idx= 51
selected idx= 52
selected idx= 53
selected idx= 54
selected idx= 55
selected idx= 56
selected idx= 57
selected idx= 58
selected idx= 59

Test set: Average loss: 2.1224 
Accuracy: 2213/10000 (22.13%)

Round 126, Train average loss 1.529 


Test set: Average loss: 2.1203 
Accuracy: 1711/10000 (17.11%)

Round 161, Train average loss 1.446 Test accuracy 17.110
[iter= 162 ] @Partition, there is no available codebook

Test set: Average loss: 2.1203 
Accuracy: 1711/10000 (17.11%)

Round 162, Train average loss 1.446 Test accuracy 17.110
[iter= 163 ] @Partition, there is no available codebook

Test set: Average loss: 2.1203 
Accuracy: 1711/10000 (17.11%)

Round 163, Train average loss 1.446 Test accuracy 17.110
[iter= 164 ] @Partition, there is no available codebook

Test set: Average loss: 2.1203 
Accuracy: 1711/10000 (17.11%)

Round 164, Train average loss 1.446 Test accuracy 17.110
[iter= 165 ] @Partition, Codebook selection
selected idx= 24
selected idx= 25
selected idx= 26
selected idx= 27
selected idx= 28
selected idx= 29
selected idx= 30
selected idx= 31
selected idx= 32
selected idx= 33
selected idx= 34
selected idx= 35

Test set: Average loss: 2.0639 
Accuracy: 2372/10000 (23.72%)

Round 165, Train average loss 1.429 

...


Test set: Average loss: 1.6929 
Accuracy: 3886/10000 (38.86%)

Round 818, Train average loss 0.930 Test accuracy 38.860
[iter= 819 ] @Partition, there is no available codebook

Test set: Average loss: 1.6929 
Accuracy: 3886/10000 (38.86%)

Round 819, Train average loss 0.930 Test accuracy 38.860
[iter= 820 ] @Partition, there is no available codebook

Test set: Average loss: 1.6929 
Accuracy: 3886/10000 (38.86%)

Round 820, Train average loss 0.930 Test accuracy 38.860
[iter= 821 ] @Partition, there is no available codebook

Test set: Average loss: 1.6929 
Accuracy: 3886/10000 (38.86%)

Round 821, Train average loss 0.930 Test accuracy 38.860
[iter= 822 ] @Partition, there is no available codebook

Test set: Average loss: 1.6929 
Accuracy: 3886/10000 (38.86%)

Round 822, Train average loss 0.930 Test accuracy 38.860
[iter= 823 ] @Partition, there is no available codebook

Test set: Average loss: 1.6929 
Accuracy: 3886/10000 (38.86%)

Round 823, Train average loss 0.930 Test accuracy 3


Test set: Average loss: 1.6585 
Accuracy: 3961/10000 (39.61%)

Round 860, Train average loss 0.861 Test accuracy 39.610
[iter= 861 ] @Partition, there is no available codebook

Test set: Average loss: 1.6585 
Accuracy: 3961/10000 (39.61%)

Round 861, Train average loss 0.861 Test accuracy 39.610
[iter= 862 ] @Partition, there is no available codebook

Test set: Average loss: 1.6585 
Accuracy: 3961/10000 (39.61%)

Round 862, Train average loss 0.861 Test accuracy 39.610
[iter= 863 ] @Partition, Codebook selection
selected idx= 12
selected idx= 13
selected idx= 14
selected idx= 15
selected idx= 16
selected idx= 17
selected idx= 18
selected idx= 19
selected idx= 20
selected idx= 21
selected idx= 22
selected idx= 23

Test set: Average loss: 1.7315 
Accuracy: 3642/10000 (36.42%)

Round 863, Train average loss 0.902 Test accuracy 36.420
[iter= 864 ] @Partition, there is no available codebook

Test set: Average loss: 1.7315 
Accuracy: 3642/10000 (36.42%)

Round 864, Train average loss 0.902 


Test set: Average loss: 1.7154 
Accuracy: 3723/10000 (37.23%)

Round 897, Train average loss 0.858 Test accuracy 37.230
[iter= 898 ] @Partition, there is no available codebook

Test set: Average loss: 1.7154 
Accuracy: 3723/10000 (37.23%)

Round 898, Train average loss 0.858 Test accuracy 37.230
[iter= 899 ] @Partition, there is no available codebook

Test set: Average loss: 1.7154 
Accuracy: 3723/10000 (37.23%)

Round 899, Train average loss 0.858 Test accuracy 37.230
[iter= 900 ] @Partition, Codebook selection
selected idx= 108
selected idx= 109
selected idx= 110
selected idx= 111
selected idx= 112
selected idx= 113
selected idx= 114
selected idx= 115
selected idx= 116
selected idx= 117
selected idx= 118
selected idx= 119

Test set: Average loss: 1.7439 
Accuracy: 3702/10000 (37.02%)

Round 900, Train average loss 0.911 Test accuracy 37.020
[iter= 901 ] @Partition, there is no available codebook

Test set: Average loss: 1.7439 
Accuracy: 3702/10000 (37.02%)

Round 901, Train average

selected idx= 118
selected idx= 119

Test set: Average loss: 1.7617 
Accuracy: 3684/10000 (36.84%)

Round 938, Train average loss 0.816 Test accuracy 36.840
[iter= 939 ] @Partition, there is no available codebook

Test set: Average loss: 1.7617 
Accuracy: 3684/10000 (36.84%)

Round 939, Train average loss 0.816 Test accuracy 36.840
[iter= 940 ] @Partition, there is no available codebook

Test set: Average loss: 1.7617 
Accuracy: 3684/10000 (36.84%)

Round 940, Train average loss 0.816 Test accuracy 36.840
[iter= 941 ] @Partition, there is no available codebook

Test set: Average loss: 1.7617 
Accuracy: 3684/10000 (36.84%)

Round 941, Train average loss 0.816 Test accuracy 36.840
[iter= 942 ] @Partition, there is no available codebook

Test set: Average loss: 1.7617 
Accuracy: 3684/10000 (36.84%)

Round 942, Train average loss 0.816 Test accuracy 36.840
[iter= 943 ] @Partition, there is no available codebook

Test set: Average loss: 1.7617 
Accuracy: 3684/10000 (36.84%)

Round 943, Trai


Test set: Average loss: 1.6584 
Accuracy: 3995/10000 (39.95%)

Round 981, Train average loss 0.791 Test accuracy 39.950
[iter= 982 ] @Partition, there is no available codebook

Test set: Average loss: 1.6584 
Accuracy: 3995/10000 (39.95%)

Round 982, Train average loss 0.791 Test accuracy 39.950
[iter= 983 ] @Partition, there is no available codebook

Test set: Average loss: 1.6584 
Accuracy: 3995/10000 (39.95%)

Round 983, Train average loss 0.791 Test accuracy 39.950
[iter= 984 ] @Partition, there is no available codebook

Test set: Average loss: 1.6584 
Accuracy: 3995/10000 (39.95%)

Round 984, Train average loss 0.791 Test accuracy 39.950
[iter= 985 ] @Partition, there is no available codebook

Test set: Average loss: 1.6584 
Accuracy: 3995/10000 (39.95%)

Round 985, Train average loss 0.791 Test accuracy 39.950
[iter= 986 ] @Partition, there is no available codebook

Test set: Average loss: 1.6584 
Accuracy: 3995/10000 (39.95%)

Round 986, Train average loss 0.791 Test accuracy 3

In [61]:
import pickle


pickle.dump(acc_test_arr_Partition_N120_K12_asymDrop, open('./results/CIFAR_NonIID_LeNet_accuracy_Partition_N120_K12_asymDrop', 'wb'), -1)

# 4. Proposed, T=6

In [7]:
from models.Nets import NIN,CNN_moderate, CNNCifar3

lr_array = [0.01]


args.local_ep = 1
args.local_bs = 50
args.weight_decay = 5e-4

N = 120
K = 12

N_trials = 3
Max_iter = 1000

args.opt = 'SGD'

args.local_ep = 1
args.local_bs = 50

acc_test_arr_Proposed_N120_K12_T6_asymDrop  = np.zeros((len(lr_array), N_trials, Max_iter))
loss_test_arr_Proposed_N120_K12_T6_asymDrop = np.zeros((len(lr_array), N_trials, Max_iter))


is_selection_applied = True
is_print = True



for trial_idx in range(N_trials):
    
    for lr_idx in range(len(lr_array)):
        
        args.lr = lr_array[lr_idx]
        
        P_proposed_T6_asymDrop = []
        
        print()
        print('Learning Rate =',args.lr)
        print()
        net_glob = CNNCifar3(args)
        net_glob = net_glob.cuda()
        print(net_glob)

        net_glob.train()

        # copy weights
        w_glob = net_glob.state_dict()
        
        for iter in range(Max_iter): #args.epochs
            w_locals, loss_locals = [], []
            
            if iter == 400 or iter == 800:
                args.lr = args.lr * 0.4

        #     u = np.random.binomial(1, 1-p, size=(N))
            u = np.ones((N,))
            for u_idx in range(N):
                p_sel = p_per_user[u_idx]
                u[u_idx] = np.random.binomial(1, 1-p_sel, size=1)[0]

            tmp = Codebook_Proposed_T6 * u

            codebook_en = 1*(np.sum(tmp,axis=1) == K)

            if np.sum(codebook_en) == 0:
                if is_print:
                    print('[iter=',iter,'] @Proposed T=6, there is no available codebook')
                p_tmp = np.zeros(N)
            else:
                if is_print:
                    print('[iter=',iter,'] @Proposed T=6, Codebook selection')
                idx_en = np.where(codebook_en == 1)

                if is_selection_applied:
                    codebook_en_num = np.sum(codebook_en)
                    Codebook_En = np.reshape(Codebook_Proposed_T6[idx_en,:],(codebook_en_num,N))

                    p_tmp = UserSelection_Codebook(P_proposed_T6_asymDrop, Codebook_En)
                else:
                    idx_sel = np.random.choice(idx_en[0], 1, replace=False)
                    p_tmp = Codebook_Proposed_T6[idx_sel[0],:]

        #                 idx_sel = np.random.choice(idx_en[0], 1, replace=False)

        #                 p_tmp = Codebook_Partition[idx_sel[0],:]

            idxs_users = np.where(p_tmp == 1)

            P_proposed_T6_asymDrop.append(p_tmp)

        #     idxs_users = np.random.choice(range(args.num_users), K, replace=False)

            if np.sum(p_tmp) == K:
                for idx in idxs_users[0]:
                    print('selected idx=',idx)
                    local = LocalUpdate(args=args, dataset=dataset_train, idxs=dict_users[idx])
                    w, loss = local.train(net=copy.deepcopy(net_glob).to(args.device))
                    w_locals.append(copy.deepcopy(w))
                    loss_locals.append(copy.deepcopy(loss))
                # update global weights
                w_glob = FedAvg(w_locals)

                # copy weight to net_glob
                net_glob.load_state_dict(w_glob)

                # print loss
                loss_avg = sum(loss_locals) / len(loss_locals)

        #         loss_train.append(loss_avg)

            acc_test, loss_test = test_img(net_glob, dataset_test, args)
            acc_test_arr_Proposed_N120_K12_T6_asymDrop[lr_idx][trial_idx][iter]  = acc_test
            loss_test_arr_Proposed_N120_K12_T6_asymDrop[lr_idx][trial_idx][iter] =loss_test
            if iter % 1 ==0:
                print('Round {:3d}, Train average loss {:.3f} Test accuracy {:.3f}'.format(iter, loss_avg,acc_test))
            #print(loss_train)


Learning Rate = 0.01

CNNCifar3(
  (conv1): Conv2d(3, 6, kernel_size=(5, 5), stride=(1, 1))
  (pool): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv2): Conv2d(6, 16, kernel_size=(5, 5), stride=(1, 1))
  (fc1): Linear(in_features=400, out_features=120, bias=True)
  (fc2): Linear(in_features=120, out_features=84, bias=True)
  (fc3): Linear(in_features=84, out_features=10, bias=True)
  (dropout): Dropout(p=0.2, inplace=False)
)
[iter= 0 ] @Proposed T=6, Codebook selection
selected idx= 0
selected idx= 1
selected idx= 2
selected idx= 3
selected idx= 20
selected idx= 21
selected idx= 22
selected idx= 23
selected idx= 64
selected idx= 65
selected idx= 66
selected idx= 67

Test set: Average loss: 2.3170 
Accuracy: 999/10000 (9.99%)

Round   0, Train average loss 1.910 Test accuracy 9.990
[iter= 1 ] @Proposed T=6, Codebook selection
selected idx= 8
selected idx= 9
selected idx= 10
selected idx= 11
selected idx= 40
selected idx= 41
selected idx= 42
selected 

selected idx= 61
selected idx= 62
selected idx= 63
selected idx= 84
selected idx= 85
selected idx= 86
selected idx= 87
selected idx= 108
selected idx= 109
selected idx= 110
selected idx= 111

Test set: Average loss: 2.0758 
Accuracy: 2156/10000 (21.56%)

Round  21, Train average loss 1.482 Test accuracy 21.560
[iter= 22 ] @Proposed T=6, Codebook selection
selected idx= 4
selected idx= 5
selected idx= 6
selected idx= 7
selected idx= 80
selected idx= 81
selected idx= 82
selected idx= 83
selected idx= 116
selected idx= 117
selected idx= 118
selected idx= 119

Test set: Average loss: 2.0696 
Accuracy: 2317/10000 (23.17%)

Round  22, Train average loss 1.424 Test accuracy 23.170
[iter= 23 ] @Proposed T=6, Codebook selection
selected idx= 4
selected idx= 5
selected idx= 6
selected idx= 7
selected idx= 52
selected idx= 53
selected idx= 54
selected idx= 55
selected idx= 92
selected idx= 93
selected idx= 94
selected idx= 95

Test set: Average loss: 2.0477 
Accuracy: 2440/10000 (24.40%)

Round  

selected idx= 25
selected idx= 26
selected idx= 27
selected idx= 64
selected idx= 65
selected idx= 66
selected idx= 67
selected idx= 116
selected idx= 117
selected idx= 118
selected idx= 119

Test set: Average loss: 1.9022 
Accuracy: 3084/10000 (30.84%)

Round  44, Train average loss 1.315 Test accuracy 30.840
[iter= 45 ] @Proposed T=6, Codebook selection
selected idx= 20
selected idx= 21
selected idx= 22
selected idx= 23
selected idx= 40
selected idx= 41
selected idx= 42
selected idx= 43
selected idx= 68
selected idx= 69
selected idx= 70
selected idx= 71

Test set: Average loss: 1.9086 
Accuracy: 3366/10000 (33.66%)

Round  45, Train average loss 1.264 Test accuracy 33.660
[iter= 46 ] @Proposed T=6, Codebook selection
selected idx= 16
selected idx= 17
selected idx= 18
selected idx= 19
selected idx= 44
selected idx= 45
selected idx= 46
selected idx= 47
selected idx= 112
selected idx= 113
selected idx= 114
selected idx= 115

Test set: Average loss: 1.8875 
Accuracy: 3305/10000 (33.05%)


selected idx= 89
selected idx= 90
selected idx= 91
selected idx= 92
selected idx= 93
selected idx= 94
selected idx= 95
selected idx= 100
selected idx= 101
selected idx= 102
selected idx= 103

Test set: Average loss: 1.7841 
Accuracy: 3483/10000 (34.83%)

Round  66, Train average loss 1.049 Test accuracy 34.830
[iter= 67 ] @Proposed T=6, Codebook selection
selected idx= 8
selected idx= 9
selected idx= 10
selected idx= 11
selected idx= 12
selected idx= 13
selected idx= 14
selected idx= 15
selected idx= 96
selected idx= 97
selected idx= 98
selected idx= 99

Test set: Average loss: 1.7732 
Accuracy: 3581/10000 (35.81%)

Round  67, Train average loss 1.065 Test accuracy 35.810
[iter= 68 ] @Proposed T=6, Codebook selection
selected idx= 40
selected idx= 41
selected idx= 42
selected idx= 43
selected idx= 68
selected idx= 69
selected idx= 70
selected idx= 71
selected idx= 104
selected idx= 105
selected idx= 106
selected idx= 107

Test set: Average loss: 1.7818 
Accuracy: 3452/10000 (34.52%)

R

selected idx= 11
selected idx= 60
selected idx= 61
selected idx= 62
selected idx= 63
selected idx= 76
selected idx= 77
selected idx= 78
selected idx= 79

Test set: Average loss: 1.7260 
Accuracy: 3669/10000 (36.69%)

Round  88, Train average loss 0.948 Test accuracy 36.690
[iter= 89 ] @Proposed T=6, Codebook selection
selected idx= 56
selected idx= 57
selected idx= 58
selected idx= 59
selected idx= 100
selected idx= 101
selected idx= 102
selected idx= 103
selected idx= 108
selected idx= 109
selected idx= 110
selected idx= 111

Test set: Average loss: 1.7232 
Accuracy: 3702/10000 (37.02%)

Round  89, Train average loss 0.893 Test accuracy 37.020
[iter= 90 ] @Proposed T=6, Codebook selection
selected idx= 24
selected idx= 25
selected idx= 26
selected idx= 27
selected idx= 36
selected idx= 37
selected idx= 38
selected idx= 39
selected idx= 48
selected idx= 49
selected idx= 50
selected idx= 51

Test set: Average loss: 1.7166 
Accuracy: 3675/10000 (36.75%)

Round  90, Train average loss 0.9

...

selected idx= 89
selected idx= 90
selected idx= 91
selected idx= 108
selected idx= 109
selected idx= 110
selected idx= 111
selected idx= 112
selected idx= 113
selected idx= 114
selected idx= 115

Test set: Average loss: 1.4563 
Accuracy: 4751/10000 (47.51%)

Round 889, Train average loss 0.326 Test accuracy 47.510
[iter= 890 ] @Proposed T=6, Codebook selection
selected idx= 16
selected idx= 17
selected idx= 18
selected idx= 19
selected idx= 60
selected idx= 61
selected idx= 62
selected idx= 63
selected idx= 96
selected idx= 97
selected idx= 98
selected idx= 99

Test set: Average loss: 1.4157 
Accuracy: 4852/10000 (48.52%)

Round 890, Train average loss 0.333 Test accuracy 48.520
[iter= 891 ] @Proposed T=6, Codebook selection
selected idx= 12
selected idx= 13
selected idx= 14
selected idx= 15
selected idx= 32
selected idx= 33
selected idx= 34
selected idx= 35
selected idx= 64
selected idx= 65
selected idx= 66
selected idx= 67

Test set: Average loss: 1.6285 
Accuracy: 4093/10000 (40.93%

selected idx= 9
selected idx= 10
selected idx= 11
selected idx= 12
selected idx= 13
selected idx= 14
selected idx= 15
selected idx= 80
selected idx= 81
selected idx= 82
selected idx= 83

Test set: Average loss: 1.4102 
Accuracy: 4974/10000 (49.74%)

Round 911, Train average loss 0.312 Test accuracy 49.740
[iter= 912 ] @Proposed T=6, Codebook selection
selected idx= 8
selected idx= 9
selected idx= 10
selected idx= 11
selected idx= 48
selected idx= 49
selected idx= 50
selected idx= 51
selected idx= 60
selected idx= 61
selected idx= 62
selected idx= 63

Test set: Average loss: 1.3457 
Accuracy: 5277/10000 (52.77%)

Round 912, Train average loss 0.273 Test accuracy 52.770
[iter= 913 ] @Proposed T=6, there is no available codebook

Test set: Average loss: 1.3457 
Accuracy: 5277/10000 (52.77%)

Round 913, Train average loss 0.273 Test accuracy 52.770
[iter= 914 ] @Proposed T=6, Codebook selection
selected idx= 48
selected idx= 49
selected idx= 50
selected idx= 51
selected idx= 88
selected id

selected idx= 5
selected idx= 6
selected idx= 7
selected idx= 80
selected idx= 81
selected idx= 82
selected idx= 83
selected idx= 88
selected idx= 89
selected idx= 90
selected idx= 91

Test set: Average loss: 1.5481 
Accuracy: 4556/10000 (45.56%)

Round 934, Train average loss 0.343 Test accuracy 45.560
[iter= 935 ] @Proposed T=6, Codebook selection
selected idx= 44
selected idx= 45
selected idx= 46
selected idx= 47
selected idx= 92
selected idx= 93
selected idx= 94
selected idx= 95
selected idx= 116
selected idx= 117
selected idx= 118
selected idx= 119

Test set: Average loss: 1.5056 
Accuracy: 4592/10000 (45.92%)

Round 935, Train average loss 0.330 Test accuracy 45.920
[iter= 936 ] @Proposed T=6, Codebook selection
selected idx= 40
selected idx= 41
selected idx= 42
selected idx= 43
selected idx= 56
selected idx= 57
selected idx= 58
selected idx= 59
selected idx= 60
selected idx= 61
selected idx= 62
selected idx= 63

Test set: Average loss: 1.3534 
Accuracy: 5201/10000 (52.01%)

Roun

selected idx= 23
selected idx= 44
selected idx= 45
selected idx= 46
selected idx= 47
selected idx= 76
selected idx= 77
selected idx= 78
selected idx= 79

Test set: Average loss: 1.5938 
Accuracy: 4337/10000 (43.37%)

Round 957, Train average loss 0.286 Test accuracy 43.370
[iter= 958 ] @Proposed T=6, Codebook selection
selected idx= 28
selected idx= 29
selected idx= 30
selected idx= 31
selected idx= 36
selected idx= 37
selected idx= 38
selected idx= 39
selected idx= 84
selected idx= 85
selected idx= 86
selected idx= 87

Test set: Average loss: 1.4892 
Accuracy: 4797/10000 (47.97%)

Round 958, Train average loss 0.351 Test accuracy 47.970
[iter= 959 ] @Proposed T=6, Codebook selection
selected idx= 20
selected idx= 21
selected idx= 22
selected idx= 23
selected idx= 52
selected idx= 53
selected idx= 54
selected idx= 55
selected idx= 64
selected idx= 65
selected idx= 66
selected idx= 67

Test set: Average loss: 1.5056 
Accuracy: 4622/10000 (46.22%)

Round 959, Train average loss 0.363 Tes

selected idx= 3
selected idx= 40
selected idx= 41
selected idx= 42
selected idx= 43
selected idx= 88
selected idx= 89
selected idx= 90
selected idx= 91

Test set: Average loss: 1.4723 
Accuracy: 4715/10000 (47.15%)

Round 979, Train average loss 0.322 Test accuracy 47.150
[iter= 980 ] @Proposed T=6, Codebook selection
selected idx= 0
selected idx= 1
selected idx= 2
selected idx= 3
selected idx= 100
selected idx= 101
selected idx= 102
selected idx= 103
selected idx= 104
selected idx= 105
selected idx= 106
selected idx= 107

Test set: Average loss: 1.4572 
Accuracy: 4726/10000 (47.26%)

Round 980, Train average loss 0.293 Test accuracy 47.260
[iter= 981 ] @Proposed T=6, Codebook selection
selected idx= 12
selected idx= 13
selected idx= 14
selected idx= 15
selected idx= 20
selected idx= 21
selected idx= 22
selected idx= 23
selected idx= 52
selected idx= 53
selected idx= 54
selected idx= 55

Test set: Average loss: 1.4496 
Accuracy: 4879/10000 (48.79%)

Round 981, Train average loss 0.318 

In [9]:
import pickle
pickle.dump(acc_test_arr_Proposed_N120_K12_T6_asymDrop, open('./results/CIFAR_NonIID_LeNet_accuracy_Proposed_N120_K12_T6_asymDrop', 'wb'), -1)

# 5. Proposed, T=4

In [10]:
from models.Nets import NIN,CNN_moderate, CNNCifar3

lr_array = [0.01]


args.local_ep = 1
args.local_bs = 50
args.weight_decay = 5e-4

N = 120
K = 12

N_trials = 3
Max_iter = 1000

args.opt = 'SGD'

args.local_ep = 1
args.local_bs = 50

acc_test_arr_Proposed_N120_K12_T4_asymDrop  = np.zeros((len(lr_array), N_trials, Max_iter))
loss_test_arr_Proposed_N120_K12_T4_asymDrop = np.zeros((len(lr_array), N_trials, Max_iter))


is_selection_applied = True
is_print = True



for trial_idx in range(N_trials):
    
    for lr_idx in range(len(lr_array)):
        
        args.lr = lr_array[lr_idx]
        
        P_proposed_T4_asymDrop = []
        
        print()
        print('Learning Rate =',args.lr)
        print()
        net_glob = CNNCifar3(args)
        net_glob = net_glob.cuda()
        print(net_glob)

        net_glob.train()

        # copy weights
        w_glob = net_glob.state_dict()
        
        for iter in range(Max_iter): #args.epochs
            w_locals, loss_locals = [], []
            
            if iter == 400 or iter == 800:
                args.lr = args.lr * 0.4

        #     u = np.random.binomial(1, 1-p, size=(N))
            u = np.ones((N,))
            for u_idx in range(N):
                p_sel = p_per_user[u_idx]
                u[u_idx] = np.random.binomial(1, 1-p_sel, size=1)[0]

            tmp = Codebook_Proposed_T4 * u

            codebook_en = 1*(np.sum(tmp,axis=1) == K)

            if np.sum(codebook_en) == 0:
                if is_print:
                    print('[iter=',iter,'] @Proposed T=4, there is no available codebook')
                p_tmp = np.zeros(N)
            else:
                if is_print:
                    print('[iter=',iter,'] @Proposed T=4, Codebook selection')
                idx_en = np.where(codebook_en == 1)

                if is_selection_applied:
                    codebook_en_num = np.sum(codebook_en)
                    Codebook_En = np.reshape(Codebook_Proposed_T4[idx_en,:],(codebook_en_num,N))

                    p_tmp = UserSelection_Codebook(P_proposed_T4_asymDrop, Codebook_En)
                else:
                    idx_sel = np.random.choice(idx_en[0], 1, replace=False)
                    p_tmp = Codebook_Proposed_T4[idx_sel[0],:]

        #                 idx_sel = np.random.choice(idx_en[0], 1, replace=False)

        #                 p_tmp = Codebook_Partition[idx_sel[0],:]

            idxs_users = np.where(p_tmp == 1)

            P_proposed_T4_asymDrop.append(p_tmp)

        #     idxs_users = np.random.choice(range(args.num_users), K, replace=False)

            if np.sum(p_tmp) == K:
                for idx in idxs_users[0]:
                    print('selected idx=',idx)
                    local = LocalUpdate(args=args, dataset=dataset_train, idxs=dict_users[idx])
                    w, loss = local.train(net=copy.deepcopy(net_glob).to(args.device))
                    w_locals.append(copy.deepcopy(w))
                    loss_locals.append(copy.deepcopy(loss))
                # update global weights
                w_glob = FedAvg(w_locals)

                # copy weight to net_glob
                net_glob.load_state_dict(w_glob)

                # print loss
                loss_avg = sum(loss_locals) / len(loss_locals)

        #         loss_train.append(loss_avg)

            acc_test, loss_test = test_img(net_glob, dataset_test, args)
            acc_test_arr_Proposed_N120_K12_T4_asymDrop[lr_idx][trial_idx][iter]  = acc_test
            loss_test_arr_Proposed_N120_K12_T4_asymDrop[lr_idx][trial_idx][iter] =loss_test
            if iter % 1 ==0:
                print('Round {:3d}, Train average loss {:.3f} Test accuracy {:.3f}'.format(iter, loss_avg,acc_test))
            #print(loss_train)


Learning Rate = 0.01

CNNCifar3(
  (conv1): Conv2d(3, 6, kernel_size=(5, 5), stride=(1, 1))
  (pool): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv2): Conv2d(6, 16, kernel_size=(5, 5), stride=(1, 1))
  (fc1): Linear(in_features=400, out_features=120, bias=True)
  (fc2): Linear(in_features=120, out_features=84, bias=True)
  (fc3): Linear(in_features=84, out_features=10, bias=True)
  (dropout): Dropout(p=0.2, inplace=False)
)
[iter= 0 ] @Proposed T=4, Codebook selection
selected idx= 20
selected idx= 21
selected idx= 22
selected idx= 23
selected idx= 28
selected idx= 29
selected idx= 30
selected idx= 31
selected idx= 60
selected idx= 61
selected idx= 62
selected idx= 63

Test set: Average loss: 2.3144 
Accuracy: 995/10000 (9.95%)

Round   0, Train average loss 1.966 Test accuracy 9.950
[iter= 1 ] @Proposed T=4, Codebook selection
selected idx= 48
selected idx= 49
selected idx= 50
selected idx= 51
selected idx= 92
selected idx= 93
selected idx= 94
sel

selected idx= 85
selected idx= 86
selected idx= 87
selected idx= 88
selected idx= 89
selected idx= 90
selected idx= 91

Test set: Average loss: 2.0781 
Accuracy: 2513/10000 (25.13%)

Round  22, Train average loss 1.447 Test accuracy 25.130
[iter= 23 ] @Proposed T=4, Codebook selection
selected idx= 0
selected idx= 1
selected idx= 2
selected idx= 3
selected idx= 32
selected idx= 33
selected idx= 34
selected idx= 35
selected idx= 56
selected idx= 57
selected idx= 58
selected idx= 59

Test set: Average loss: 2.1093 
Accuracy: 1940/10000 (19.40%)

Round  23, Train average loss 1.485 Test accuracy 19.400
[iter= 24 ] @Proposed T=4, Codebook selection
selected idx= 16
selected idx= 17
selected idx= 18
selected idx= 19
selected idx= 32
selected idx= 33
selected idx= 34
selected idx= 35
selected idx= 80
selected idx= 81
selected idx= 82
selected idx= 83

Test set: Average loss: 2.0675 
Accuracy: 2311/10000 (23.11%)

Round  24, Train average loss 1.455 Test accuracy 23.110
[iter= 25 ] @Proposed 

selected idx= 83
selected idx= 108
selected idx= 109
selected idx= 110
selected idx= 111

Test set: Average loss: 1.9399 
Accuracy: 2954/10000 (29.54%)

Round  44, Train average loss 1.293 Test accuracy 29.540
[iter= 45 ] @Proposed T=4, there is no available codebook

Test set: Average loss: 1.9399 
Accuracy: 2954/10000 (29.54%)

Round  45, Train average loss 1.293 Test accuracy 29.540
[iter= 46 ] @Proposed T=4, Codebook selection
selected idx= 20
selected idx= 21
selected idx= 22
selected idx= 23
selected idx= 36
selected idx= 37
selected idx= 38
selected idx= 39
selected idx= 64
selected idx= 65
selected idx= 66
selected idx= 67

Test set: Average loss: 1.9702 
Accuracy: 2794/10000 (27.94%)

Round  46, Train average loss 1.311 Test accuracy 27.940
[iter= 47 ] @Proposed T=4, Codebook selection
selected idx= 4
selected idx= 5
selected idx= 6
selected idx= 7
selected idx= 8
selected idx= 9
selected idx= 10
selected idx= 11
selected idx= 108
selected idx= 109
selected idx= 110
selected i

selected idx= 13
selected idx= 14
selected idx= 15
selected idx= 76
selected idx= 77
selected idx= 78
selected idx= 79
selected idx= 116
selected idx= 117
selected idx= 118
selected idx= 119

Test set: Average loss: 1.7748 
Accuracy: 3615/10000 (36.15%)

Round  67, Train average loss 1.093 Test accuracy 36.150
[iter= 68 ] @Proposed T=4, Codebook selection
selected idx= 44
selected idx= 45
selected idx= 46
selected idx= 47
selected idx= 52
selected idx= 53
selected idx= 54
selected idx= 55
selected idx= 56
selected idx= 57
selected idx= 58
selected idx= 59

Test set: Average loss: 1.7719 
Accuracy: 3749/10000 (37.49%)

Round  68, Train average loss 1.007 Test accuracy 37.490
[iter= 69 ] @Proposed T=4, Codebook selection
selected idx= 12
selected idx= 13
selected idx= 14
selected idx= 15
selected idx= 64
selected idx= 65
selected idx= 66
selected idx= 67
selected idx= 80
selected idx= 81
selected idx= 82
selected idx= 83

Test set: Average loss: 1.7960 
Accuracy: 3450/10000 (34.50%)

Rou

selected idx= 25
selected idx= 26
selected idx= 27
selected idx= 48
selected idx= 49
selected idx= 50
selected idx= 51
selected idx= 52
selected idx= 53
selected idx= 54
selected idx= 55

Test set: Average loss: 1.7373 
Accuracy: 3776/10000 (37.76%)

Round  90, Train average loss 0.941 Test accuracy 37.760
[iter= 91 ] @Proposed T=4, Codebook selection
selected idx= 0
selected idx= 1
selected idx= 2
selected idx= 3
selected idx= 8
selected idx= 9
selected idx= 10
selected idx= 11
selected idx= 100
selected idx= 101
selected idx= 102
selected idx= 103

Test set: Average loss: 1.7280 
Accuracy: 3756/10000 (37.56%)

Round  91, Train average loss 0.918 Test accuracy 37.560
[iter= 92 ] @Proposed T=4, Codebook selection
selected idx= 12
selected idx= 13
selected idx= 14
selected idx= 15
selected idx= 44
selected idx= 45
selected idx= 46
selected idx= 47
selected idx= 68
selected idx= 69
selected idx= 70
selected idx= 71

Test set: Average loss: 1.7273 
Accuracy: 3660/10000 (36.60%)

Round  92

...


Test set: Average loss: 1.3954 
Accuracy: 4908/10000 (49.08%)

Round 890, Train average loss 0.332 Test accuracy 49.080
[iter= 891 ] @Proposed T=4, Codebook selection
selected idx= 52
selected idx= 53
selected idx= 54
selected idx= 55
selected idx= 80
selected idx= 81
selected idx= 82
selected idx= 83
selected idx= 84
selected idx= 85
selected idx= 86
selected idx= 87

Test set: Average loss: 1.6437 
Accuracy: 4098/10000 (40.98%)

Round 891, Train average loss 0.294 Test accuracy 40.980
[iter= 892 ] @Proposed T=4, Codebook selection
selected idx= 8
selected idx= 9
selected idx= 10
selected idx= 11
selected idx= 40
selected idx= 41
selected idx= 42
selected idx= 43
selected idx= 108
selected idx= 109
selected idx= 110
selected idx= 111

Test set: Average loss: 1.4577 
Accuracy: 4771/10000 (47.71%)

Round 892, Train average loss 0.305 Test accuracy 47.710
[iter= 893 ] @Proposed T=4, Codebook selection
selected idx= 40
selected idx= 41
selected idx= 42
selected idx= 43
selected idx= 48
s


Test set: Average loss: 1.5135 
Accuracy: 4608/10000 (46.08%)

Round 912, Train average loss 0.333 Test accuracy 46.080
[iter= 913 ] @Proposed T=4, Codebook selection
selected idx= 4
selected idx= 5
selected idx= 6
selected idx= 7
selected idx= 20
selected idx= 21
selected idx= 22
selected idx= 23
selected idx= 56
selected idx= 57
selected idx= 58
selected idx= 59

Test set: Average loss: 1.4339 
Accuracy: 4861/10000 (48.61%)

Round 913, Train average loss 0.283 Test accuracy 48.610
[iter= 914 ] @Proposed T=4, Codebook selection
selected idx= 48
selected idx= 49
selected idx= 50
selected idx= 51
selected idx= 72
selected idx= 73
selected idx= 74
selected idx= 75
selected idx= 88
selected idx= 89
selected idx= 90
selected idx= 91

Test set: Average loss: 1.3869 
Accuracy: 5005/10000 (50.05%)

Round 914, Train average loss 0.273 Test accuracy 50.050
[iter= 915 ] @Proposed T=4, Codebook selection
selected idx= 68
selected idx= 69
selected idx= 70
selected idx= 71
selected idx= 76
selecte


Test set: Average loss: 1.6205 
Accuracy: 4273/10000 (42.73%)

Round 934, Train average loss 0.344 Test accuracy 42.730
[iter= 935 ] @Proposed T=4, Codebook selection
selected idx= 4
selected idx= 5
selected idx= 6
selected idx= 7
selected idx= 60
selected idx= 61
selected idx= 62
selected idx= 63
selected idx= 104
selected idx= 105
selected idx= 106
selected idx= 107

Test set: Average loss: 1.4259 
Accuracy: 4826/10000 (48.26%)

Round 935, Train average loss 0.399 Test accuracy 48.260
[iter= 936 ] @Proposed T=4, Codebook selection
selected idx= 28
selected idx= 29
selected idx= 30
selected idx= 31
selected idx= 32
selected idx= 33
selected idx= 34
selected idx= 35
selected idx= 68
selected idx= 69
selected idx= 70
selected idx= 71

Test set: Average loss: 1.3945 
Accuracy: 4978/10000 (49.78%)

Round 936, Train average loss 0.321 Test accuracy 49.780
[iter= 937 ] @Proposed T=4, Codebook selection
selected idx= 0
selected idx= 1
selected idx= 2
selected idx= 3
selected idx= 20
selecte


Test set: Average loss: 1.4473 
Accuracy: 4825/10000 (48.25%)

Round 956, Train average loss 0.274 Test accuracy 48.250
[iter= 957 ] @Proposed T=4, Codebook selection
selected idx= 40
selected idx= 41
selected idx= 42
selected idx= 43
selected idx= 88
selected idx= 89
selected idx= 90
selected idx= 91
selected idx= 116
selected idx= 117
selected idx= 118
selected idx= 119

Test set: Average loss: 1.5041 
Accuracy: 4673/10000 (46.73%)

Round 957, Train average loss 0.287 Test accuracy 46.730
[iter= 958 ] @Proposed T=4, Codebook selection
selected idx= 80
selected idx= 81
selected idx= 82
selected idx= 83
selected idx= 100
selected idx= 101
selected idx= 102
selected idx= 103
selected idx= 112
selected idx= 113
selected idx= 114
selected idx= 115

Test set: Average loss: 1.4713 
Accuracy: 4760/10000 (47.60%)

Round 958, Train average loss 0.357 Test accuracy 47.600
[iter= 959 ] @Proposed T=4, Codebook selection
selected idx= 8
selected idx= 9
selected idx= 10
selected idx= 11
selected i

selected idx= 99

Test set: Average loss: 1.4191 
Accuracy: 4729/10000 (47.29%)

Round 978, Train average loss 0.352 Test accuracy 47.290
[iter= 979 ] @Proposed T=4, Codebook selection
selected idx= 4
selected idx= 5
selected idx= 6
selected idx= 7
selected idx= 16
selected idx= 17
selected idx= 18
selected idx= 19
selected idx= 100
selected idx= 101
selected idx= 102
selected idx= 103

Test set: Average loss: 1.3614 
Accuracy: 4992/10000 (49.92%)

Round 979, Train average loss 0.299 Test accuracy 49.920
[iter= 980 ] @Proposed T=4, Codebook selection
selected idx= 20
selected idx= 21
selected idx= 22
selected idx= 23
selected idx= 28
selected idx= 29
selected idx= 30
selected idx= 31
selected idx= 92
selected idx= 93
selected idx= 94
selected idx= 95

Test set: Average loss: 1.4440 
Accuracy: 4702/10000 (47.02%)

Round 980, Train average loss 0.284 Test accuracy 47.020
[iter= 981 ] @Proposed T=4, Codebook selection
selected idx= 48
selected idx= 49
selected idx= 50
selected idx= 51
sel

# 6. Proposed, T=3

In [11]:
from models.Nets import NIN,CNN_moderate, CNNCifar3

lr_array = [0.01]


args.local_ep = 1
args.local_bs = 50
args.weight_decay = 5e-4

N = 120
K = 12

N_trials = 3
Max_iter = 1000

args.opt = 'SGD'

args.local_ep = 1
args.local_bs = 50
# lr_array = [0.03, 0.01, 0.003]

acc_test_arr_Proposed_N120_K12_T3_asymDrop  = np.zeros((len(lr_array), N_trials, Max_iter))
loss_test_arr_Proposed_N120_K12_T3_asymDrop = np.zeros((len(lr_array), N_trials, Max_iter))


is_selection_applied = True
is_print = True



for trial_idx in range(N_trials):
    
    for lr_idx in range(len(lr_array)):
        
        args.lr = lr_array[lr_idx]
        
        P_proposed_T3_asymDrop = []
        
        print()
        print('Learning Rate =',args.lr)
        print()
        net_glob = CNNCifar3(args)
        net_glob = net_glob.cuda()
        print(net_glob)

        net_glob.train()

        # copy weights
        w_glob = net_glob.state_dict()
        
        for iter in range(Max_iter): #args.epochs
            w_locals, loss_locals = [], []
            
            if iter == 400 or iter == 800:
                args.lr = args.lr * 0.4

        #     u = np.random.binomial(1, 1-p, size=(N))
            u = np.ones((N,))
            for u_idx in range(N):
                p_sel = p_per_user[u_idx]
                u[u_idx] = np.random.binomial(1, 1-p_sel, size=1)[0]

            tmp = Codebook_Proposed_T3 * u

            codebook_en = 1*(np.sum(tmp,axis=1) == K)

            if np.sum(codebook_en) == 0:
                if is_print:
                    print('[iter=',iter,'] @Proposed T=3, there is no available codebook')
                p_tmp = np.zeros(N)
            else:
                if is_print:
                    print('[iter=',iter,'] @Proposed T=3, Codebook selection')
                idx_en = np.where(codebook_en == 1)

                if is_selection_applied:
                    codebook_en_num = np.sum(codebook_en)
                    Codebook_En = np.reshape(Codebook_Proposed_T3[idx_en,:],(codebook_en_num,N))

                    p_tmp = UserSelection_Codebook(P_proposed_T3_asymDrop, Codebook_En)
                else:
                    idx_sel = np.random.choice(idx_en[0], 1, replace=False)
                    p_tmp = Codebook_Proposed_T3[idx_sel[0],:]

        #                 idx_sel = np.random.choice(idx_en[0], 1, replace=False)

        #                 p_tmp = Codebook_Partition[idx_sel[0],:]

            idxs_users = np.where(p_tmp == 1)

            P_proposed_T3_asymDrop.append(p_tmp)

        #     idxs_users = np.random.choice(range(args.num_users), K, replace=False)

            if np.sum(p_tmp) == K:
                for idx in idxs_users[0]:
                    print('selected idx=',idx)
                    local = LocalUpdate(args=args, dataset=dataset_train, idxs=dict_users[idx])
                    w, loss = local.train(net=copy.deepcopy(net_glob).to(args.device))
                    w_locals.append(copy.deepcopy(w))
                    loss_locals.append(copy.deepcopy(loss))
                # update global weights
                w_glob = FedAvg(w_locals)

                # copy weight to net_glob
                net_glob.load_state_dict(w_glob)

                # print loss
                loss_avg = sum(loss_locals) / len(loss_locals)

        #         loss_train.append(loss_avg)

            acc_test, loss_test = test_img(net_glob, dataset_test, args)
            acc_test_arr_Proposed_N120_K12_T3_asymDrop[lr_idx][trial_idx][iter]  = acc_test
            loss_test_arr_Proposed_N120_K12_T3_asymDrop[lr_idx][trial_idx][iter] =loss_test
            if iter % 1 ==0:
                print('Round {:3d}, Train average loss {:.3f} Test accuracy {:.3f}'.format(iter, loss_avg,acc_test))
            #print(loss_train)


Learning Rate = 0.01

CNNCifar3(
  (conv1): Conv2d(3, 6, kernel_size=(5, 5), stride=(1, 1))
  (pool): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
  (conv2): Conv2d(6, 16, kernel_size=(5, 5), stride=(1, 1))
  (fc1): Linear(in_features=400, out_features=120, bias=True)
  (fc2): Linear(in_features=120, out_features=84, bias=True)
  (fc3): Linear(in_features=84, out_features=10, bias=True)
  (dropout): Dropout(p=0.2, inplace=False)
)
[iter= 0 ] @Proposed T=3, Codebook selection
selected idx= 63
selected idx= 64
selected idx= 65
selected idx= 69
selected idx= 70
selected idx= 71
selected idx= 87
selected idx= 88
selected idx= 89
selected idx= 96
selected idx= 97
selected idx= 98

Test set: Average loss: 2.3223 
Accuracy: 1000/10000 (10.00%)

Round   0, Train average loss 1.899 Test accuracy 10.000
[iter= 1 ] @Proposed T=3, Codebook selection
selected idx= 6
selected idx= 7
selected idx= 8
selected idx= 51
selected idx= 52
selected idx= 53
selected idx= 84
sel

selected idx= 43
selected idx= 44
selected idx= 51
selected idx= 52
selected idx= 53
selected idx= 84
selected idx= 85
selected idx= 86
selected idx= 114
selected idx= 115
selected idx= 116

Test set: Average loss: 2.0728 
Accuracy: 1989/10000 (19.89%)

Round  21, Train average loss 1.439 Test accuracy 19.890
[iter= 22 ] @Proposed T=3, Codebook selection
selected idx= 0
selected idx= 1
selected idx= 2
selected idx= 60
selected idx= 61
selected idx= 62
selected idx= 75
selected idx= 76
selected idx= 77
selected idx= 87
selected idx= 88
selected idx= 89

Test set: Average loss: 2.0992 
Accuracy: 2649/10000 (26.49%)

Round  22, Train average loss 1.423 Test accuracy 26.490
[iter= 23 ] @Proposed T=3, Codebook selection
selected idx= 33
selected idx= 34
selected idx= 35
selected idx= 72
selected idx= 73
selected idx= 74
selected idx= 78
selected idx= 79
selected idx= 80
selected idx= 90
selected idx= 91
selected idx= 92

Test set: Average loss: 2.0587 
Accuracy: 2317/10000 (23.17%)

Round  

selected idx= 51
selected idx= 52
selected idx= 53
selected idx= 75
selected idx= 76
selected idx= 77
selected idx= 87
selected idx= 88
selected idx= 89

Test set: Average loss: 1.8878 
Accuracy: 3369/10000 (33.69%)

Round  43, Train average loss 1.241 Test accuracy 33.690
[iter= 44 ] @Proposed T=3, Codebook selection
selected idx= 45
selected idx= 46
selected idx= 47
selected idx= 48
selected idx= 49
selected idx= 50
selected idx= 72
selected idx= 73
selected idx= 74
selected idx= 90
selected idx= 91
selected idx= 92

Test set: Average loss: 1.9298 
Accuracy: 3222/10000 (32.22%)

Round  44, Train average loss 1.236 Test accuracy 32.220
[iter= 45 ] @Proposed T=3, Codebook selection
selected idx= 9
selected idx= 10
selected idx= 11
selected idx= 15
selected idx= 16
selected idx= 17
selected idx= 84
selected idx= 85
selected idx= 86
selected idx= 99
selected idx= 100
selected idx= 101

Test set: Average loss: 1.9217 
Accuracy: 2750/10000 (27.50%)

Round  45, Train average loss 1.245 Test

selected idx= 97
selected idx= 98
selected idx= 102
selected idx= 103
selected idx= 104
selected idx= 108
selected idx= 109
selected idx= 110

Test set: Average loss: 1.7494 
Accuracy: 3461/10000 (34.61%)

Round  65, Train average loss 1.023 Test accuracy 34.610
[iter= 66 ] @Proposed T=3, Codebook selection
selected idx= 6
selected idx= 7
selected idx= 8
selected idx= 30
selected idx= 31
selected idx= 32
selected idx= 72
selected idx= 73
selected idx= 74
selected idx= 75
selected idx= 76
selected idx= 77

Test set: Average loss: 1.7537 
Accuracy: 3746/10000 (37.46%)

Round  66, Train average loss 1.018 Test accuracy 37.460
[iter= 67 ] @Proposed T=3, Codebook selection
selected idx= 0
selected idx= 1
selected idx= 2
selected idx= 9
selected idx= 10
selected idx= 11
selected idx= 15
selected idx= 16
selected idx= 17
selected idx= 75
selected idx= 76
selected idx= 77

Test set: Average loss: 1.7642 
Accuracy: 3772/10000 (37.72%)

Round  67, Train average loss 1.035 Test accuracy 37.720
[i

selected idx= 26
selected idx= 42
selected idx= 43
selected idx= 44
selected idx= 105
selected idx= 106
selected idx= 107

Test set: Average loss: 1.7272 
Accuracy: 3739/10000 (37.39%)

Round  87, Train average loss 0.903 Test accuracy 37.390
[iter= 88 ] @Proposed T=3, Codebook selection
selected idx= 18
selected idx= 19
selected idx= 20
selected idx= 33
selected idx= 34
selected idx= 35
selected idx= 57
selected idx= 58
selected idx= 59
selected idx= 72
selected idx= 73
selected idx= 74

Test set: Average loss: 1.7637 
Accuracy: 3416/10000 (34.16%)

Round  88, Train average loss 0.913 Test accuracy 34.160
[iter= 89 ] @Proposed T=3, Codebook selection
selected idx= 24
selected idx= 25
selected idx= 26
selected idx= 39
selected idx= 40
selected idx= 41
selected idx= 48
selected idx= 49
selected idx= 50
selected idx= 63
selected idx= 64
selected idx= 65

Test set: Average loss: 1.7480 
Accuracy: 3647/10000 (36.47%)

Round  89, Train average loss 0.926 Test accuracy 36.470
[iter= 90 ] @Pr

...

selected idx= 87
selected idx= 88
selected idx= 89

Test set: Average loss: 1.3399 
Accuracy: 5266/10000 (52.66%)

Round 902, Train average loss 0.298 Test accuracy 52.660
[iter= 903 ] @Proposed T=3, Codebook selection
selected idx= 30
selected idx= 31
selected idx= 32
selected idx= 33
selected idx= 34
selected idx= 35
selected idx= 36
selected idx= 37
selected idx= 38
selected idx= 96
selected idx= 97
selected idx= 98

Test set: Average loss: 1.3694 
Accuracy: 5058/10000 (50.58%)

Round 903, Train average loss 0.289 Test accuracy 50.580
[iter= 904 ] @Proposed T=3, Codebook selection
selected idx= 51
selected idx= 52
selected idx= 53
selected idx= 69
selected idx= 70
selected idx= 71
selected idx= 90
selected idx= 91
selected idx= 92
selected idx= 99
selected idx= 100
selected idx= 101

Test set: Average loss: 1.6012 
Accuracy: 4242/10000 (42.42%)

Round 904, Train average loss 0.364 Test accuracy 42.420
[iter= 905 ] @Proposed T=3, Codebook selection
selected idx= 0
selected idx= 1
sel

selected idx= 108
selected idx= 109
selected idx= 110

Test set: Average loss: 1.4271 
Accuracy: 4699/10000 (46.99%)

Round 924, Train average loss 0.332 Test accuracy 46.990
[iter= 925 ] @Proposed T=3, Codebook selection
selected idx= 30
selected idx= 31
selected idx= 32
selected idx= 57
selected idx= 58
selected idx= 59
selected idx= 72
selected idx= 73
selected idx= 74
selected idx= 87
selected idx= 88
selected idx= 89

Test set: Average loss: 1.3383 
Accuracy: 5118/10000 (51.18%)

Round 925, Train average loss 0.283 Test accuracy 51.180
[iter= 926 ] @Proposed T=3, Codebook selection
selected idx= 63
selected idx= 64
selected idx= 65
selected idx= 90
selected idx= 91
selected idx= 92
selected idx= 96
selected idx= 97
selected idx= 98
selected idx= 102
selected idx= 103
selected idx= 104

Test set: Average loss: 1.5517 
Accuracy: 4368/10000 (43.68%)

Round 926, Train average loss 0.342 Test accuracy 43.680
[iter= 927 ] @Proposed T=3, Codebook selection
selected idx= 15
selected idx= 

selected idx= 62
selected idx= 66
selected idx= 67
selected idx= 68

Test set: Average loss: 1.4841 
Accuracy: 4519/10000 (45.19%)

Round 946, Train average loss 0.282 Test accuracy 45.190
[iter= 947 ] @Proposed T=3, Codebook selection
selected idx= 36
selected idx= 37
selected idx= 38
selected idx= 45
selected idx= 46
selected idx= 47
selected idx= 81
selected idx= 82
selected idx= 83
selected idx= 96
selected idx= 97
selected idx= 98

Test set: Average loss: 1.3691 
Accuracy: 4965/10000 (49.65%)

Round 947, Train average loss 0.299 Test accuracy 49.650
[iter= 948 ] @Proposed T=3, Codebook selection
selected idx= 54
selected idx= 55
selected idx= 56
selected idx= 57
selected idx= 58
selected idx= 59
selected idx= 60
selected idx= 61
selected idx= 62
selected idx= 111
selected idx= 112
selected idx= 113

Test set: Average loss: 1.3579 
Accuracy: 5148/10000 (51.48%)

Round 948, Train average loss 0.254 Test accuracy 51.480
[iter= 949 ] @Proposed T=3, Codebook selection
selected idx= 9
s

selected idx= 69
selected idx= 70
selected idx= 71

Test set: Average loss: 1.4191 
Accuracy: 4871/10000 (48.71%)

Round 968, Train average loss 0.310 Test accuracy 48.710
[iter= 969 ] @Proposed T=3, Codebook selection
selected idx= 30
selected idx= 31
selected idx= 32
selected idx= 48
selected idx= 49
selected idx= 50
selected idx= 84
selected idx= 85
selected idx= 86
selected idx= 117
selected idx= 118
selected idx= 119

Test set: Average loss: 1.3991 
Accuracy: 4916/10000 (49.16%)

Round 969, Train average loss 0.270 Test accuracy 49.160
[iter= 970 ] @Proposed T=3, Codebook selection
selected idx= 21
selected idx= 22
selected idx= 23
selected idx= 57
selected idx= 58
selected idx= 59
selected idx= 78
selected idx= 79
selected idx= 80
selected idx= 114
selected idx= 115
selected idx= 116

Test set: Average loss: 1.6282 
Accuracy: 4209/10000 (42.09%)

Round 970, Train average loss 0.290 Test accuracy 42.090
[iter= 971 ] @Proposed T=3, Codebook selection
selected idx= 12
selected idx= 

selected idx= 79
selected idx= 80

Test set: Average loss: 1.6935 
Accuracy: 4006/10000 (40.06%)

Round 990, Train average loss 0.309 Test accuracy 40.060
[iter= 991 ] @Proposed T=3, Codebook selection
selected idx= 3
selected idx= 4
selected idx= 5
selected idx= 18
selected idx= 19
selected idx= 20
selected idx= 57
selected idx= 58
selected idx= 59
selected idx= 102
selected idx= 103
selected idx= 104

Test set: Average loss: 1.3637 
Accuracy: 5049/10000 (50.49%)

Round 991, Train average loss 0.291 Test accuracy 50.490
[iter= 992 ] @Proposed T=3, Codebook selection
selected idx= 63
selected idx= 64
selected idx= 65
selected idx= 66
selected idx= 67
selected idx= 68
selected idx= 93
selected idx= 94
selected idx= 95
selected idx= 114
selected idx= 115
selected idx= 116

Test set: Average loss: 1.3768 
Accuracy: 5014/10000 (50.14%)

Round 992, Train average loss 0.312 Test accuracy 50.140
[iter= 993 ] @Proposed T=3, Codebook selection
selected idx= 6
selected idx= 7
selected idx= 8
sel

In [12]:
import pickle

pickle.dump(acc_test_arr_Proposed_N120_K12_T4_asymDrop, open('./results/CIFAR_NonIID_LeNet_accuracy_Proposed_N120_K12_T4_asymDrop', 'wb'), -1)
pickle.dump(acc_test_arr_Proposed_N120_K12_T3_asymDrop, open('./results/CIFAR_NonIID_LeNet_accuracy_Proposed_N120_K12_T3_asymDrop', 'wb'), -1)